## Table of Contents

[1. Import News Data](#Import)<br>
[2. Sentiment Analysis](#Sentiment)<br>
&emsp;&emsp;[2.1 Harvard IV-4 Dictionary](#Harvard)<br>
&emsp;&emsp;[2.2 Loughran and McDonald Dictionary](#Maccy)<br>
[3. Notes](#Notes)<br>

In [12]:
# Import libraries 
import numpy as np
import pandas as pd
import os

from datetime import datetime

<a id='Import'></a>
## Import News Data

In [13]:
zip_lst = ['Data1.zip', 'Data2.zip', 'Data3.zip']
df_news = pd.DataFrame()

for zip_dt in zip_lst:
    df_news = pd.concat([df_news, pd.read_csv(zip_dt)], axis=0)

# Remove entries without content
df_news['content'].replace('empty string', np.nan, inplace=True)
df_news = df_news.loc[~df_news['content'].isna(), ]

# Reset index
df_news.reset_index(drop=True, inplace=True)

df_news.shape

(38515, 7)

In [85]:
df_news.head(10)

ticker       date     time  \
0    MMM  Feb-19-21  08:11AM   
1    MMM  Feb-18-21  11:00AM   
2    MMM  Feb-17-21  09:37AM   
3    MMM  Feb-16-21  04:18PM   
4    MMM  Feb-16-21  03:58PM   
5    MMM  Feb-16-21  08:00AM   
6    MMM  Feb-12-21  05:12PM   
7    MMM  Feb-09-21  02:35PM   
8    MMM  Feb-09-21  11:07AM   
9    MMM  Feb-09-21  11:07AM   

                                            headline                  news  \
0  Did You Acquire 3M (MMM) Before February 9, 20...           PR Newswire   
1  3M launches New 3M Clean & Protect Certified B...           PR Newswire   
2                               ROCE Insights For 3M              Benzinga   
3  Why 3M is spending $1 billion to help improve ...         Yahoo Finance   
4  3M CEO on the company's plans to invest $1B to...   Yahoo Finance Video   
5  3M to Invest $1 Billion to Achieve Carbon Neut...           PR Newswire   
6    First Eagle Investment's Top 4th-Quarter Trades         GuruFocus.com   
7              3M Announces Upcoming Investor Events           PR Newswire   
8  New 3M Polisher ST reduces the number of bioph...           PR Newswire   
9  New 3M Polisher ST reduces the number of bioph...             CNW Group   

                                             content               site  
0  SAN DIEGO, Feb. 19, 2021 /PRNewswire/ -- Johns...  finance.yahoo.com  
1  The new four-part program promotes cleanliness...  finance.yahoo.com  
2  3M (NYSE:MMM) posted a 3.14% decrease in earni...  finance.yahoo.com  
3  3M Chairman and CEO Mike Roman said it's time ...  finance.yahoo.com  
4  Mike Roman, 3M Chairman and CEO, joined Yahoo ...  finance.yahoo.com  
5  ST. PAUL, Minn., Feb. 16, 2021 /PRNewswire/ --...  finance.yahoo.com  
6  - By Graham GriffinFirst Eagle Investment (Tra...  finance.yahoo.com  
7  ST. PAUL, Minn., Feb. 9, 2021 /PRNewswire/ -- ...  finance.yahoo.com  
8  ST. PAUL, Minn., Feb. 9, 2021 /PRNewswire/ -- ...  finance.yahoo.com  
9  ST. PAUL, Minn., Feb. 9, 2021 /CNW/ -- 3M Heal...  finance.yahoo.com

In [84]:
# Import labelled validation data 
valid = pd.read_csv('data/news_sample.csv', index_col=0)
valid.head()

ticker       date     time  \
3174      PM  Feb-04-21  10:33AM   
8657    CTLT  Sep-09-20  10:14AM   
16599    ZTS  Feb-12-21  08:38AM   
5695     AZO  Sep-18-20  06:25AM   
7327     SEE  May-28-20  09:08AM   

                                                headline              news  \
3174   Philip Morris (PM) Q4 Earnings Beat Estimates ...             Zacks   
8657   Radius Completes Enrollment in Phase III Osteo...             Zacks   
16599  Is a Surprise Coming for Zoetis (ZTS) This Ear...             Zacks   
5695   If You Had Bought AutoZone (NYSE:AZO) Shares T...   Simply Wall St.   
7327   Sealed Air (SEE) Stock Down 18% YTD: Will it B...             Zacks   

                                                 content               site  \
3174   Philip Morris International Inc. PM reported f...  finance.yahoo.com   
8657   Radius Health, Inc. RDUS announced the complet...  finance.yahoo.com   
16599  Investors are always looking for stocks that a...  finance.yahoo.com   
5695   The worst result, after buying shares in a com...  finance.yahoo.com   
7327   Sealed Air Corporation’s SEE focus on innovati...  finance.yahoo.com   

       sent  
3174      1  
8657      1  
16599     1  
5695      1  
7327      0

<a id='Sentiment'></a>
## Sentiment Analysis

In [18]:
# Pysentiment contains 2 dictionaries- Harvard and Loughran and Mcdonald
import pysentiment2 as ps

<a id='Harvard'></a>
### Harvard Sentiment Analysis

##### Using headlines

In [120]:
# Data exploration- sentiment for each headline
hiv4 = ps.HIV4()
# Text is pre-processed by default tokenizer in library
for i in df_news['headline']:
    tokens = hiv4.tokenize(i)
    score = hiv4.get_score(tokens)
    print(score)

{'Positive': 3, 'Negative': 1, 'Polarity': 0.49999987500003124, 'Subjectivity': 0.3636363305785154}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.33333327777778704}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09090908264462885}
{'Positive': 4, 'Negative': 1, 'Polarity': 0.599999880000024, 'Subjectivity': 0.6249999218750099}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 4, 'Negative': 0, 'Polarity': 0.9999997500000625, 'Subjectivity': 0.23529410380622917}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.399999920000016}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.19999998666666757}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjec

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.22222219753086697}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.4285713673469475}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.22222219753086697}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09999999000000101}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subje

{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.599999880000024}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.24999996875000394}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.33333327777778704}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.285714244897965}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'P

...

{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.33333327777778704}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.33333327777778704}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.599999880000024}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.499999750000125}
{'Positive': 2, 'Negative': 1, 'Polarity': 0.33333322222225925, 'Subjectivity': 0.7499998125000469}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.399999920000016}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.19999998000000202}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{

{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.33333327777778704}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.285714244897965}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.33333327777778704}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 2, 'Polarity': -0.33333322222225925, 'Subjectivity': 0.4285713673469475}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.9999990000010001}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.399999920000016}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.499999750000125}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, '

{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.09090908677685969}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.08333332638888948}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.08333332638888948}
{'Positive': 4, 'Negative': 0, 'Polarity': 0.9999997500000625, 'Subjectivity': 0.24999998437500096}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.14285713265306196}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.49999987500003124}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.4285713673469475}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.22222219753086697}
{'Positive': 4, 'Negative': 0, 'Polarity': 0.9999997500000625, 'Subjectivity': 0.2666666488888901}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity'

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.49999991666668053}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 3, 'Negative': 0, 'Polarity': 0.9999996666667778, 'Subjectivity': 0.599999880000024}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.6666664444445185}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 1, 'Negative': 0, 'Polarit

In [181]:
# Predict sentiment score
scores = []
for i in valid['headline']:
    tokens = hiv4.tokenize(i)
    score = hiv4.get_score(tokens)
    scores.append(score['Polarity']) # Take only polarity score as proxy for sentiment
    
sc = np.asarray(scores)
# Add to validation dataframe
valid['score'] = sc
valid.head()

ticker       date     time  \
3174      PM  Feb-04-21  10:33AM   
8657    CTLT  Sep-09-20  10:14AM   
16599    ZTS  Feb-12-21  08:38AM   
5695     AZO  Sep-18-20  06:25AM   
7327     SEE  May-28-20  09:08AM   

                                                headline              news  \
3174   Philip Morris (PM) Q4 Earnings Beat Estimates ...             Zacks   
8657   Radius Completes Enrollment in Phase III Osteo...             Zacks   
16599  Is a Surprise Coming for Zoetis (ZTS) This Ear...             Zacks   
5695   If You Had Bought AutoZone (NYSE:AZO) Shares T...   Simply Wall St.   
7327   Sealed Air (SEE) Stock Down 18% YTD: Will it B...             Zacks   

                                                 content               site  \
3174   Philip Morris International Inc. PM reported f...  finance.yahoo.com   
8657   Radius Health, Inc. RDUS announced the complet...  finance.yahoo.com   
16599  Investors are always looking for stocks that a...  finance.yahoo.com   
5695   The worst result, after buying shares in a com...  finance.yahoo.com   
7327   Sealed Air Corporation’s SEE focus on innovati...  finance.yahoo.com   

       sent     score  
3174    1.0 -0.999999  
8657    1.0  0.000000  
16599   1.0  0.999999  
5695    1.0  0.999999  
7327    1.0  0.000000

In [235]:
# Calculate correlation between pred and true 
valid['sent'].corr(valid['score']) # Returning nan 

# Check if the variance is zero 
from statistics import variance 
import math
math.sqrt(variance(valid['sent']))
math.sqrt(variance(valid['score']))

# Carry out same execution using scipy 
from scipy.stats import spearmanr
spearmanr(valid['sent'], valid['score'])

SpearmanrResult(correlation=nan, pvalue=nan)

##### Using article content

In [106]:
hiv4 = ps.HIV4()
# Text is pre-processed by default tokenizer in library
for i in df_news['content']:
    tokens = hiv4.tokenize(i)
    score = hiv4.get_score(tokens)
    print(score)

{'Positive': 52, 'Negative': 14, 'Polarity': 0.5757575670339763, 'Subjectivity': 0.31428571278911566}
{'Positive': 136, 'Negative': 9, 'Polarity': 0.8758620629250893, 'Subjectivity': 0.3929539284743796}
{'Positive': 50, 'Negative': 6, 'Polarity': 0.7857142716836738, 'Subjectivity': 0.3499999978125}
{'Positive': 45, 'Negative': 15, 'Polarity': 0.4999999916666668, 'Subjectivity': 0.20134228120354938}
{'Positive': 126, 'Negative': 36, 'Polarity': 0.5555555521262003, 'Subjectivity': 0.2519440120498538}
{'Positive': 256, 'Negative': 54, 'Polarity': 0.6516129011238293, 'Subjectivity': 0.3163265302894627}
{'Positive': 122, 'Negative': 25, 'Polarity': 0.659863941089361, 'Subjectivity': 0.21459853983270286}
{'Positive': 17, 'Negative': 3, 'Polarity': 0.6999999650000017, 'Subjectivity': 0.18691588610358986}
{'Positive': 84, 'Negative': 7, 'Polarity': 0.8461538368554523, 'Subjectivity': 0.3297101437329343}
{'Positive': 89, 'Negative': 7, 'Polarity': 0.8541666577690974, 'Subjectivity': 0.311688310

{'Positive': 33, 'Negative': 7, 'Polarity': 0.6499999837500005, 'Subjectivity': 0.26845637403720557}
{'Positive': 77, 'Negative': 28, 'Polarity': 0.46666666222222225, 'Subjectivity': 0.2884615376690617}
{'Positive': 75, 'Negative': 26, 'Polarity': 0.48514851004803455, 'Subjectivity': 0.2845070414520928}
{'Positive': 66, 'Negative': 23, 'Polarity': 0.4831460619871229, 'Subjectivity': 0.2564841491167604}
{'Positive': 91, 'Negative': 26, 'Polarity': 0.5555555508072175, 'Subjectivity': 0.2896039596791981}
{'Positive': 100, 'Negative': 25, 'Polarity': 0.5999999952, 'Subjectivity': 0.2723311540907818}
{'Positive': 86, 'Negative': 30, 'Polarity': 0.482758616527943, 'Subjectivity': 0.28999999927500003}
{'Positive': 95, 'Negative': 50, 'Polarity': 0.31034482544589775, 'Subjectivity': 0.2725563904651196}
{'Positive': 81, 'Negative': 33, 'Polarity': 0.4210526278855033, 'Subjectivity': 0.2760290550217214}
{'Positive': 92, 'Negative': 21, 'Polarity': 0.628318578510455, 'Subjectivity': 0.31741572944

{'Positive': 108, 'Negative': 64, 'Polarity': 0.2558139520010817, 'Subjectivity': 0.2582582578704831}
{'Positive': 186, 'Negative': 48, 'Polarity': 0.589743587223318, 'Subjectivity': 0.2535211264858926}
{'Positive': 30, 'Negative': 6, 'Polarity': 0.6666666481481487, 'Subjectivity': 0.1698113199537202}
{'Positive': 107, 'Negative': 52, 'Polarity': 0.34591194750998777, 'Subjectivity': 0.23555555520658436}
{'Positive': 308, 'Negative': 155, 'Polarity': 0.33045356300118023, 'Subjectivity': 0.2751039808228734}
{'Positive': 33, 'Negative': 9, 'Polarity': 0.5714285578231296, 'Subjectivity': 0.19626168132587998}
{'Positive': 51, 'Negative': 9, 'Polarity': 0.6999999883333335, 'Subjectivity': 0.20905923272104798}
{'Positive': 89, 'Negative': 40, 'Polarity': 0.3798449582957755, 'Subjectivity': 0.2287234038497812}
{'Positive': 38, 'Negative': 6, 'Polarity': 0.7272727107438021, 'Subjectivity': 0.19730941615556316}
{'Positive': 99, 'Negative': 17, 'Polarity': 0.7068965456302022, 'Subjectivity': 0.26

{'Positive': 169, 'Negative': 42, 'Polarity': 0.60189573174457, 'Subjectivity': 0.31398809477085105}
{'Positive': 106, 'Negative': 14, 'Polarity': 0.7666666602777779, 'Subjectivity': 0.32171581683186107}
{'Positive': 95, 'Negative': 26, 'Polarity': 0.5702479291715047, 'Subjectivity': 0.2358674459339816}
{'Positive': 274, 'Negative': 50, 'Polarity': 0.691358022557537, 'Subjectivity': 0.29589041068868455}
{'Positive': 194, 'Negative': 48, 'Polarity': 0.6033057826309679, 'Subjectivity': 0.32352941133217994}
{'Positive': 1083, 'Negative': 395, 'Polarity': 0.46549391037517324, 'Subjectivity': 0.3013866231033061}
{'Positive': 90, 'Negative': 17, 'Polarity': 0.6822429842781029, 'Subjectivity': 0.30397727186370094}
{'Positive': 231, 'Negative': 66, 'Polarity': 0.5555555536849981, 'Subjectivity': 0.3481828835308524}
{'Positive': 173, 'Negative': 41, 'Polarity': 0.6168224270241943, 'Subjectivity': 0.2884097031153508}
{'Positive': 50, 'Negative': 6, 'Polarity': 0.7857142716836738, 'Subjectivity':

{'Positive': 40, 'Negative': 8, 'Polarity': 0.6666666527777781, 'Subjectivity': 0.2651933687005891}
{'Positive': 37, 'Negative': 13, 'Polarity': 0.47999999040000024, 'Subjectivity': 0.23148148040980795}
{'Positive': 93, 'Negative': 30, 'Polarity': 0.5121951177870315, 'Subjectivity': 0.243083003472168}
{'Positive': 105, 'Negative': 44, 'Polarity': 0.4093959704067385, 'Subjectivity': 0.22473604792649163}
{'Positive': 47, 'Negative': 8, 'Polarity': 0.7090908961983474, 'Subjectivity': 0.25462962845078874}
{'Positive': 50, 'Negative': 9, 'Polarity': 0.6949152424590637, 'Subjectivity': 0.22014925290989085}
{'Positive': 13, 'Negative': 3, 'Polarity': 0.6249999609375024, 'Subjectivity': 0.20253164300592857}
{'Positive': 32, 'Negative': 26, 'Polarity': 0.10344827407847804, 'Subjectivity': 0.231999999072}
{'Positive': 29, 'Negative': 23, 'Polarity': 0.11538461316568052, 'Subjectivity': 0.23008849455713057}
{'Positive': 47, 'Negative': 14, 'Polarity': 0.5409835976887934, 'Subjectivity': 0.2155477

...

{'Positive': 154, 'Negative': 35, 'Polarity': 0.6296296262982559, 'Subjectivity': 0.2578444744094891}
{'Positive': 40, 'Negative': 11, 'Polarity': 0.5686274398308345, 'Subjectivity': 0.26153846019723864}
{'Positive': 76, 'Negative': 16, 'Polarity': 0.6521739059546314, 'Subjectivity': 0.3345454533289256}
{'Positive': 10, 'Negative': 0, 'Polarity': 0.99999990000001, 'Subjectivity': 0.238095232426304}
{'Positive': 82, 'Negative': 36, 'Polarity': 0.38983050517092793, 'Subjectivity': 0.2448132775003874}
{'Positive': 51, 'Negative': 9, 'Polarity': 0.6999999883333335, 'Subjectivity': 0.3333333314814815}
{'Positive': 94, 'Negative': 10, 'Polarity': 0.8076922999260356, 'Subjectivity': 0.3611111098572531}
{'Positive': 45, 'Negative': 20, 'Polarity': 0.384615378698225, 'Subjectivity': 0.23550724552352448}
{'Positive': 58, 'Negative': 5, 'Polarity': 0.841269827916352, 'Subjectivity': 0.39374999753906254}
{'Positive': 95, 'Negative': 12, 'Polarity': 0.7757009273298979, 'Subjectivity': 0.35197368305

{'Positive': 29, 'Negative': 14, 'Polarity': 0.3488372011898325, 'Subjectivity': 0.24712643536134232}
{'Positive': 40, 'Negative': 6, 'Polarity': 0.7391304187145562, 'Subjectivity': 0.2513661188449939}
{'Positive': 18, 'Negative': 10, 'Polarity': 0.28571427551020445, 'Subjectivity': 0.2799999972}
{'Positive': 215, 'Negative': 34, 'Polarity': 0.7269076276027806, 'Subjectivity': 0.2599164924217991}
{'Positive': 41, 'Negative': 9, 'Polarity': 0.6399999872000003, 'Subjectivity': 0.2304147454819597}
{'Positive': 60, 'Negative': 10, 'Polarity': 0.7142857040816328, 'Subjectivity': 0.33018867768778926}
{'Positive': 70, 'Negative': 25, 'Polarity': 0.47368420554016627, 'Subjectivity': 0.24421593767553743}
{'Positive': 59, 'Negative': 9, 'Polarity': 0.7352941068339102, 'Subjectivity': 0.21316614353239455}
{'Positive': 36, 'Negative': 5, 'Polarity': 0.7560975425342064, 'Subjectivity': 0.23033707735765688}
{'Positive': 167, 'Negative': 66, 'Polarity': 0.4334763929893717, 'Subjectivity': 0.252164501

{'Positive': 93, 'Negative': 45, 'Polarity': 0.34782608443604285, 'Subjectivity': 0.2804878043079516}
{'Positive': 18, 'Negative': 4, 'Polarity': 0.6363636074380178, 'Subjectivity': 0.2894736804016621}
{'Positive': 31, 'Negative': 12, 'Polarity': 0.44186045484045455, 'Subjectivity': 0.24431818043001033}
{'Positive': 66, 'Negative': 9, 'Polarity': 0.7599999898666668, 'Subjectivity': 0.31779660882289573}
{'Positive': 79, 'Negative': 23, 'Polarity': 0.5490196024605921, 'Subjectivity': 0.21428571383553421}
{'Positive': 36, 'Negative': 28, 'Polarity': 0.12499999804687503, 'Subjectivity': 0.24060150285488158}
{'Positive': 118, 'Negative': 95, 'Polarity': 0.10798122015032291, 'Subjectivity': 0.23101952252600919}
{'Positive': 44, 'Negative': 6, 'Polarity': 0.7599999848000003, 'Subjectivity': 0.19531249923706054}
{'Positive': 22, 'Negative': 13, 'Polarity': 0.2571428497959186, 'Subjectivity': 0.174999999125}
{'Positive': 29, 'Negative': 15, 'Polarity': 0.3181818109504134, 'Subjectivity': 0.2199

{'Positive': 573, 'Negative': 206, 'Polarity': 0.47111681582655096, 'Subjectivity': 0.3869845999071115}
{'Positive': 61, 'Negative': 18, 'Polarity': 0.544303790578433, 'Subjectivity': 0.26510067025134004}
{'Positive': 77, 'Negative': 26, 'Polarity': 0.49514562626072206, 'Subjectivity': 0.2893258418839162}
{'Positive': 75, 'Negative': 23, 'Polarity': 0.5306122394835486, 'Subjectivity': 0.2525773189366564}
{'Positive': 158, 'Negative': 41, 'Polarity': 0.5879396955379915, 'Subjectivity': 0.27832167793241724}
{'Positive': 124, 'Negative': 24, 'Polarity': 0.6756756711102996, 'Subjectivity': 0.2614840984779433}
{'Positive': 125, 'Negative': 34, 'Polarity': 0.5723270404256161, 'Subjectivity': 0.27797202748606287}
{'Positive': 69, 'Negative': 10, 'Polarity': 0.7468354335843617, 'Subjectivity': 0.2791519424764949}
{'Positive': 28, 'Negative': 1, 'Polarity': 0.9310344506539844, 'Subjectivity': 0.13744075764246086}
{'Positive': 49, 'Negative': 6, 'Polarity': 0.781818167603306, 'Subjectivity': 0.2

KeyboardInterrupt: 

<a id='Maccy'></a>
### Loughran and McDonald Dictionary

In [202]:
lm = ps.LM()
for i in df_news['headline']:
    tokens = lm.tokenize(i)
    score = lm.get_score(tokens)
    print(score)

{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.1818181652892577}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.33333322222225925}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Sub

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'P

{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09090908264462885}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.07142856632653098}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.14285713265306196}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.08333332638888948}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.11111109876543349}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Sub

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.09999999000000101}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.05263157617728546}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, '

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 2, 'Polarity': -0.33333322222225925, 'Subjectivity': 0.21428569897959293}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.13333332444444504}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.16666665277777895}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.11764705190311459}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 2, 'Polarity': -0.99999950000025, 'Subjectivity': 0.24999996875000394}
{'Positive': 0, 'Ne

...

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.16666663888889352}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity'

{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.33333327777778704}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.285714244897965}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.999999000001

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09090908264462885}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.16666665277777895}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.199999960000008}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.999999

{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 1, 'Polarity': -0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.09999999000000101}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 3, 'Negative': 1, 'Polarity': 0.49999987500003124, 'Subjectivity': 0.39999996000000404}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.11111109876543349}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 1, 'Polarity': 0.0, 'Subjectivity': 0.285714244897965}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.1428571224489825}
{'Positive': 0, 'Negative': 0, 'Polarity

{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.24999993750001562}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 1, 'Negative': 0, 'Polarity': 0.9999990000010001, 'Subjectivity': 0.12499998437500197}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive': 2, 'Negative': 0, 'Polarity': 0.99999950000025, 'Subjectivity': 0.22222219753086697}
{'Positive': 0, 'Negative': 0, 'Polarity': 0.0, 'Subjectivity': 0.0}
{'Positive':